In [3]:
import pandas as pd

# 1. Text Extraction

#### Using PyMuPDF

In [42]:
import fitz  # Import the PyMuPDF library

def extract_text_pymupdf(pdf_path):
    doc = fitz.open(pdf_path)  # Open the PDF file
    text = ""  # Initialize an empty string to store text

    for page in doc:  # Iterate through each page
        text += page.get_text()  # Extract text from the page and append it

    doc.close()  # Close the document
    return text

# Example usage
pdf_path = '/Users/juliamarkusiewicz/Downloads/PDF_Mining_Julia/Jaarrekening-Momo-Medical-Holding-B.V.-2022.pdf'
text = extract_text_pymupdf(pdf_path)
text_data = extract_text_pymupdf(pdf_path)
print(text)

The accountant's compilation report has been issued
 
 
 
 
 
Consolidated financial statements 2022
Momo Medical Holding B.V.
DELFT
Table of contents
Consolidated balance sheet . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . 2
Consolidated profit and loss account . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . 4
Notes to the consolidated financial statements . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . 5
Balance sheet . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . 14
Profit and loss account . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . 16
Notes to the financial statements . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . 17
Specifications to the financial statements . . . . . . . . . . . . . . . . . . . . . . . . 

#### Using  PyPDF2

In [11]:
import PyPDF2

def extract_text_pypdf2(pdf_path):
    text = ""  # Initialize an empty string to store text
    with open(pdf_path, 'rb') as file:  # Open the PDF file in binary mode
        reader = PyPDF2.PdfReader(file)  # Create a PDF reader object

        for page in reader.pages:  # Iterate through each page
            text += page.extract_text() + "\n"  # Extract text and append it

    return text

# Example usage
pdf_path = '/Users/juliamarkusiewicz/Downloads/PDF_Mining_Julia/Jaarrekening-Momo-Medical-Holding-B.V.-2022.pdf'
text = extract_text_pypdf2(pdf_path)
print(text)

T h e
a c c o u n t a n t ' s
c o m p i l a t i o n
r e p o r t
h a s
b e e n
i s s u e d
     Consolidated financial statements 2022Momo Medical Holding B.V.DELFT
Table of contentsConsolidated balance sheet. . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . 2Consolidated profit and loss account. . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . 4Notes to the consolidated financial statements. . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . 5Balance sheet. . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . .14Profit and loss account. . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . .16Notes to the financial statements. . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . 17Specifications to the financial statements. . . . . . . . . . . . . . . . .

## Table Extraction

In [5]:
from tabula import read_pdf

def extract_tables_tabula(pdf_path):
    # This function returns a list of DataFrames, one for each page
    dfs = read_pdf(pdf_path, pages='all', multiple_tables=True)

    for i, df in enumerate(dfs):
        print(f"Table {i+1}:")
        print(df)  # Print each table
        # You can also save the DataFrame to a CSV or Excel
        # df.to_csv(f'table_{i+1}.csv') # Uncomment to save to CSV

# Example usage
pdf_path = '/Users/juliamarkusiewicz/Downloads/PDF_Mining_Julia/Jaarrekening-Momo-Medical-Holding-B.V.-2022.pdf'
extract_tables_tabula(pdf_path)

Error importing jpype dependencies. Fallback to subprocess.
No module named 'jpype'


Table 1:
                    Other tangible assets  784,641  214,361
0  Total of property, plant and equipment  828,933  228,080
1             Total of non-current assets  828,933  228,080
2                                     NaN      NaN      NaN
3                          Current assets      NaN      NaN
4                             Inventories      NaN      NaN
5           Raw materials and consumables  266,885   63,896
6          Inventories under construction   42,450   25,064
7                Finished and trade goods  125,005   61,284
8                    Total of inventories  434,340  150,244
Table 2:
               Depreciation of other tangible assets  77,081  35,727
0  Total of depreciation of property, plant and e...  84,937  40,039
1  Total of amortisation of intangible assets and...  84,937  40,039
2                      property, plant and equipment     NaN     NaN
3                           Other operating expenses     NaN     NaN
4                                Acco

## Extracting and Categorising data 

In [39]:
text_data = """
Property, plant and equipment
 
Machinery
44,292
13,719
Other tangible assets
784,641
214,361
Total of property, plant and equipment
828,933
228,080
Total of non-current assets
828,933
228,080
"""

In [46]:
def is_number(s: str) -> Tuple[int, bool]:
    if s.startswith("(") and s.endswith(")"):
        s = s[1:-1]
    num = s.replace(",", "").replace(".", "")
    return num, num.isdigit()

def parse_adjusted_financial_text(text):
    # Split the text into lines
    lines = text.strip().split("\n")
    
    # Initialize an empty list to store our parsed data
    parsed_data = []
    
    # Initialize empty strings for current description and values
    current_description = ""
    value_2022 = ""
    
    # Iterate over each line in the text
    for line in lines:
        # Check if line is a description or a value
        maybe_num, is_num = is_number(line)
        if is_num:
            # If it's a digit, it's a value
            if value_2022 == "":
                # If the first value is not yet set, set it as 2022 value
                value_2022 = maybe_num
            else:
                # If the first value is set, this line must be the 2021 value
                # Append the description and values to our data list
                print([current_description.strip().lower(), int(value_2022.replace(",", "")), int(line.replace(",", ""))])
                parsed_data.append([current_description.strip().lower(), int(value_2022.replace(",", "")), int(line.replace(",", ""))])
                # Reset the values for the next set of data
                current_description = ""
                value_2022 = ""
        else:
            # If it's not a digit, it's a description
            # Accumulate descriptions until we reach a digit
            if current_description:
                current_description += " " + line
            else:
                current_description = line
                
    # Convert the parsed data into a DataFrame
    return pd.DataFrame(parsed_data, columns=['Description', '2022 EUR', '2021 EUR'])

In [47]:
# Parse the adjusted text data
df_parsed = parse_adjusted_financial_text(text_data)

# Display the parsed DataFrame
print(df_parsed)

["the accountant's compilation report has been issued           consolidated financial statements 2022 momo medical holding b.v. delft table of contents consolidated balance sheet . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . 2 consolidated profit and loss account . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . 4 notes to the consolidated financial statements . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . 5 balance sheet . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . 14 profit and loss account . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . 16 notes to the financial statements . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . 17 specifications to the financial statements . . . . . . . . . . . . . . . . . . . . . . . 

In [25]:
def parse_financial_text_enhanced(text):
    lines = text.strip().split("\n")
    
    parsed_data = []
    current_description_lines = []
    values = []
    
    for line in lines:
        # Check if the line is numeric (possibly a value)
        if line.replace(",", "").replace(".", "").isdigit():
            values.append(int(line.replace(",", "")))  # Convert to int, removing commas
            
            # If we have two values collected, we should also have a description ready
            if len(values) == 2:
                description = " ".join(current_description_lines).strip()
                parsed_data.append([description] + values)
                # Reset for the next item
                current_description_lines = []
                values = []
        else:
            # If it's not a numeric line, it could be a part of a description
            if values:
                # If we've already encountered a numeric value, this line starts a new description
                # Handle any previously collected description and values
                if current_description_lines:
                    description = " ".join(current_description_lines).strip()
                    parsed_data.append([description, values[0], None])  # Assume missing second value
                    values = []
                current_description_lines = [line]
            else:
                # Continue accumulating description lines
                current_description_lines.append(line)

    # Handling any remaining items after loop completion
    if current_description_lines and values:
        description = " ".join(current_description_lines).strip()
        parsed_data.append([description] + values)

    return pd.DataFrame(parsed_data, columns=['Description', '2022 EUR', '2021 EUR'])
# Parse the adjusted text data
df_parsed = parse_adjusted_financial_text(text_data)

# Display the parsed DataFrame
print(df_parsed)

In [33]:
def is_numeric(line):
    # Remove commas and check if it's a digit, accounting for parentheses
    return line.replace(",", "").replace("(", "").replace(")", "").isdigit()

def parse_text_to_df_v2(text):
    lines = text.strip().split('\n')
    data = []
    description_lines = []
    numeric_values = []

    for line in lines:
        line = line.strip()
        if not line:  # Skip empty lines
            continue

        if is_numeric(line) or line == '-':
            # Convert parentheses to negative numbers
            if line.startswith("(") and line.endswith(")"):
                line = "-" + line[1:-1]
            value = int(line.replace(",", "")) if line != '-' else None
            numeric_values.append(value)

            # Check if it's time to save the collected description and values
            if len(numeric_values) == 2:
                description = " ".join(description_lines)
                data.append([description] + numeric_values)
                description_lines, numeric_values = [], []
        else:
            # New description starts if we were collecting numeric values
            if numeric_values:
                if len(numeric_values) == 1:  # Missing second value
                    numeric_values.append(None)
                description = " ".join(description_lines)
                data.append([description] + numeric_values)
                description_lines, numeric_values = [line], []
            else:
                description_lines.append(line)

    # Handle the last item
    if description_lines:
        if len(numeric_values) == 1:
            numeric_values.append(None)  # Ensure two values for the last item
        description = " ".join(description_lines)
        data.append([description] + numeric_values)

    df = pd.DataFrame(data, columns=["Description", "2022 EUR", "2021 EUR"])
    return df



df_parsed = parse_text_to_df_v2(text_data)
print(df_parsed)

# 2. Data Cleaning + Preprocessing

In [15]:
import pandas as pd

def clean_dataframe(df):
    # Drop rows where all elements are NaN
    df = df.dropna(how='all')
    # Reset index after dropping rows
    df = df.reset_index(drop=True)
    # Optionally, set the first row as header if needed
    df.columns = df.iloc[0]  # This assumes the first row is the header
    df = df.drop(0)  # Drop the original header row
    # Convert data types, here assuming all other columns should be numeric
    df = df.apply(pd.to_numeric, errors='ignore')
    return df

### Classifying Data 

Before standardize- all lowercase, no spaces .....

list of variables of interest ?- both dutch and english or pre-trained models with libraries

In [16]:
def classify_table(df):
    # Example of simple keyword-based classification
    if 'Total of inventories' in df.columns:
        return 'Inventory'
    elif 'Total of non-current assets' in df.columns:
        return 'Non-Current Assets'


    else:
        return 'Unknown'

# 3. Data Validation

look for Huggingface models, pretrained ml for financial statements

In [17]:
#Consistency check ...

# Balance sheet validation rule: Assets = Liabilities + Equity
if total_assets == total_liabilities + equity:
    print("The balance sheet balances.")
else:
    print("There is a discrepancy in the balance sheet.")
    